In [4]:
#import modules
import json
import pandas as pd
from binance.client import Client
from dotenv import load_dotenv
from envs import env
import time
import re
import os
import datetime
from datetime import timedelta
import statistics

In [5]:
#import classes from ./ folder
import postgresdbAccess

In [19]:
#read fibonacci retracements  from json
with open('fibLvl.json') as file:
    fibLvl = json.load(file)

In [36]:
def backtest():
    #initiate empty open positions
    openPositions = {}
    #initiate postgresdb class
    postgres = postgresdbAccess.postgresAccess()
    #get unique simbol list
    sql = ("SELECT distinct symbol FROM " + dbTable + ";")
    uniqueSymbol = pd.DataFrame(postgres.sqlQuery(sql))
    uniqueSymbol = uniqueSymbol[0]
    #initiate empty percent bar
    percentBar = 0
    #loop over every symbol in symbol list
    for symbol in uniqueSymbol:
        #print progress
        print(percentBar, " / ", len(uniqueSymbol))
        percentBar = percentBar + 1
        #skip if symbol is not to be considered
        #null askprice is sorted out with crawler already
        if not (symbol.endswith(baseCurrency) and
               len(symbol) < 11):
            continue
        #check if open position was left over from last symbol and simulate close
        if openPositions:
            #prepare sql for close
            openPositions['resultPercent'] = ((row[4] - openPositions['askPrice']) / openPositions['askPrice']) * 100 - brokerFees * 2.55
            openPositions['stopId'] = row[0]
            closeSql = ("UPDATE " + dbTable + " SET" +
            " startId = '" + str(int(openPositions['startId'])) +
            "', fibLevel = '" + str(openPositions['fibLevel']) +
            "', midId = '" + str(int(openPositions['id'])) +
            "', corValue = '" + str(openPositions['corValue']) +
            "', takeProfit = '" + str(openPositions['takeProfit']) +
            "', stopLoss = '" + str(openPositions['stopLoss']) +  
            "', resultpercent = '" + str(openPositions['resultPercent']) +
            "', stopid = '" + str(openPositions['stopId']) +
            "' WHERE id = '" + str(int(openPositions['id'])) +
            "';")
            postgres.sqlUpdate(closeSql)
            openPositions = {}
        #query for every line for symbol
        sql = ("SELECT id, time, symbol, askprice, " +
               "bidprice, highprice, quotevolume, " +
               "pricechangepercent, weightedavgprice, openprice" +
            " FROM " + dbTable + " WHERE" +
            " symbol like '" + symbol + "' order by id;")
        print(sql)
        bigData = pd.DataFrame(postgres.sqlQuery(sql))
        bigData[0] = pd.to_numeric(bigData[0], errors='coerce', downcast='float')
        bigData[1] = pd.to_datetime(bigData[1])
        bigData[3] = pd.to_numeric(bigData[3], errors='coerce', downcast='float')
        bigData[4] = pd.to_numeric(bigData[4], errors='coerce', downcast='float')
        bigData[6] = pd.to_numeric(bigData[6], errors='coerce', downcast='float')
        bigData[7] = pd.to_numeric(bigData[7], errors='coerce', downcast='float')
        bigData[8] = pd.to_numeric(bigData[8], errors='coerce', downcast='float')
        bigData[9] = pd.to_numeric(bigData[9], errors='coerce', downcast='float')
        #get start of timedelta
        bigData[5] = bigData[1] - timedelta(hours=33)
        bigData[10] = bigData[1] - timedelta(hours=15)
        bigData[11] = bigData[1] - timedelta(hours=5)
        bigData[12] = bigData[1] - timedelta(hours=1)
        #loop over every row
        for index, row in bigData.iterrows():
            before_start_date = bigData[1] <= row[5]
            if len(bigData.loc[before_start_date]) > 0:
                #get data for consideration
                after_start_date = bigData[1] >= row[5]
                before_end_date = bigData[1] <= row[1]
                between_two_dates = after_start_date & before_end_date
                fibDates = bigData.loc[between_two_dates]
                diff = fibDates[3].max() - fibDates[3].min()
                # calculate fibRetracements
                fibRetracement = pd.DataFrame(fibLvl)
                maxAsk = fibDates[3].max()
                for lvl in fibRetracement:
                    fibRetracement[1] =  maxAsk - diff * fibRetracement[0]
                    fibRetracement[2] = fibRetracement[1] * 0.9995
                    fibRetracement[3] = fibRetracement[1] * 1.0005
                #calculate corvalue
                corValue = fibDates[0].corr(fibDates[3])
                before_start_date1 = bigData[1] <= row[5]
                bigData[10] = bigData[1] - timedelta(hours=15)
                after_start_date1 = bigData[1] >= row[10]
                before_end_date1 = bigData[1] <= row[1]
                between_two_dates1 = after_start_date1 & before_end_date1
                fibDates1 = bigData.loc[between_two_dates]
                corValue1 = fibDates1[0].corr(fibDates1[3])
                
                before_start_date2 = bigData[1] <= row[5]
                bigData[11] = bigData[1] - timedelta(hours=5)
                after_start_date2 = bigData[1] >= row[11]
                before_end_date2 = bigData[1] <= row[1]
                between_two_dates2 = after_start_date2 & before_end_date2
                fibDates2 = bigData.loc[between_two_dates2]
                corValue2 = fibDates2[0].corr(fibDates2[3])
                
                before_start_date3 = bigData[1] <= row[5]
                bigData[12] = bigData[1] - timedelta(hours=1)
                after_start_date3 = bigData[1] >= row[12]
                before_end_date3 = bigData[1] <= row[1]
                between_two_dates3 = after_start_date3 & before_end_date3
                fibDates3 = bigData.loc[between_two_dates3]
                corValue3 = fibDates3[0].corr(fibDates3[3])
                
                #if an open position exists, check if it can be closed
                if openPositions:
                    if (row[3] < openPositions['stopLoss'] or
                        row[3] > openPositions['takeProfit']):
                        #prepare sql for close
                        openPositions['resultPercent'] = ((row[4] - openPositions['askPrice']) / openPositions['askPrice']) * 100 - brokerFees * 3.5
                        openPositions['stopId'] = row[0]
                        closeSql = ("UPDATE " + dbTable + " SET" +
                        " startId = '" + str(int(openPositions['startId'])) +
                        "', fibLevel = '" + str(openPositions['fibLevel']) +
                        "', midId = '" + str(int(openPositions['id'])) +
                        "', corValue = '" + str(openPositions['corValue']) +
                        "', takeProfit = '" + str(openPositions['takeProfit']) +
                        "', stopLoss = '" + str(openPositions['stopLoss']) +  
                        "', resultpercent = '" + str(openPositions['resultPercent']) +
                        "', stopid = '" + str(openPositions['stopId']) +
                        "', stdev = '" + str(openPositions['stDev']) +
                        "' WHERE id = '" + str(int(openPositions['id'])) +
                        "';")
                        #update database
                        postgres.sqlUpdate(closeSql)
                        #clear open position
                        openPositions = {}
                else:
                    #loop over considered fibonacciretracements
                    for i in [7]:
                        #check if buy requirements are met
                        if (corValue >= 0 and
                            corValue1 >= 0 and
                            corValue2 >= 0 and
                            corValue3 >= 0 and
                            row[3] < fibRetracement[3][i] and
                            row[3] > fibRetracement[2][i]):
                            openPositions['startId'] = fibDates[0].min()
                            openPositions['id'] = row[0]
                            openPositions['bidPrice'] = row[4]
                            openPositions['fibLevel'] = i
                            openPositions['symbol'] = symbol
                            openPositions['askPrice'] = row[3]
                            openPositions['corValue'] = corValue
                            openPositions['stDev'] = statistics.stdev(fibDates[8])
                            openPositions['takeProfit'] = fibRetracement[3][i+4]
                            openPositions['stopLoss'] = fibRetracement[2][i-1]
    #close database connection
    postgres.databaseClose()

In [37]:
testTables = [{"table":"backtesting","currency":"BNB"},
             {"table":"backtesting","currency":"BTC"},
             {"table":"backtesting","currency":"ETH"},
             {"table":"backtesting","currency":"ADA"}]
for iteration in testTables:
    load_dotenv('../.env')
    try:
        liveVolume=env("liveVolume")
        apiSecret=env('apiSecret')
        apiKey=env('apiKey')
        dbTable=iteration["table"]
        baseCurrency=iteration["currency"]
        brokerFees=float(env('brokerFees'))
        liveTrading=env("liveTrading", 'False').lower() in ('true', '1', 't')
    except KeyError:
        print("No env variables set.")
        sys.exit(1)
    client = Client(apiKey, apiSecret, {'timeout':600})
    backtest()

0  /  752
1  /  752
2  /  752
3  /  752
4  /  752
5  /  752
SELECT id, time, symbol, askprice, bidprice, highprice, quotevolume, pricechangepercent, weightedavgprice, openprice FROM backtesting WHERE symbol like 'ADXBNB' order by id;
             0                                1       2    3    4   \
2        1662.0 2021-09-14 20:09:53.513917+00:00  ADXBNB  0.0  0.0   
3        2410.0 2021-09-14 20:10:53.160949+00:00  ADXBNB  0.0  0.0   
4        3158.0 2021-09-14 20:11:53.579602+00:00  ADXBNB  0.0  0.0   
5        3906.0 2021-09-14 20:12:53.987061+00:00  ADXBNB  0.0  0.0   
6        4654.0 2021-09-14 20:13:54.302781+00:00  ADXBNB  0.0  0.0   
...         ...                              ...     ...  ...  ...   
1977  1478962.0 2021-09-16 05:04:53.226509+00:00  ADXBNB  0.0  0.0   
1978  1479710.0 2021-09-16 05:05:53.421499+00:00  ADXBNB  0.0  0.0   
1979  1480458.0 2021-09-16 05:06:54.264035+00:00  ADXBNB  0.0  0.0   
1980  1481206.0 2021-09-16 05:07:53.890294+00:00  ADXBNB  0.0  0.0

nannannannan
             0                                1       2    3    4   \
18      13630.0 2021-09-14 20:25:53.539262+00:00  ADXBNB  0.0  0.0   
19      14378.0 2021-09-14 20:26:54.581638+00:00  ADXBNB  0.0  0.0   
20      15126.0 2021-09-14 20:27:54.273375+00:00  ADXBNB  0.0  0.0   
21      15874.0 2021-09-14 20:28:53.642340+00:00  ADXBNB  0.0  0.0   
22      16622.0 2021-09-14 20:29:52.604967+00:00  ADXBNB  0.0  0.0   
...         ...                              ...     ...  ...  ...   
1985  1484946.0 2021-09-16 05:17:06.236734+00:00  ADXBNB  0.0  0.0   
1986  1485694.0 2021-09-16 05:19:06.484247+00:00  ADXBNB  0.0  0.0   
1987  1486442.0 2021-09-16 05:21:06.787285+00:00  ADXBNB  0.0  0.0   
1988  1487190.0 2021-09-16 05:23:07.004558+00:00  ADXBNB  0.0  0.0   
1989  1487938.0 2021-09-16 05:25:06.582377+00:00  ADXBNB  0.0  0.0   

                                   5    6    7    8    9   \
18   2021-09-13 11:25:53.539262+00:00  0.0  0.0  0.0  0.0   
19   2021-09-13 11:26:54

nannannannan
             0                                1       2    3    4   \
30      22606.0 2021-09-14 20:37:54.144403+00:00  ADXBNB  0.0  0.0   
31      23354.0 2021-09-14 20:38:56.328289+00:00  ADXBNB  0.0  0.0   
32      24102.0 2021-09-14 20:39:53.267329+00:00  ADXBNB  0.0  0.0   
33      24850.0 2021-09-14 20:40:53.186527+00:00  ADXBNB  0.0  0.0   
34      25598.0 2021-09-14 20:41:53.613442+00:00  ADXBNB  0.0  0.0   
...         ...                              ...     ...  ...  ...   
1991  1489434.0 2021-09-16 05:29:06.747967+00:00  ADXBNB  0.0  0.0   
1992  1490182.0 2021-09-16 05:31:06.060476+00:00  ADXBNB  0.0  0.0   
1993  1490930.0 2021-09-16 05:33:06.258224+00:00  ADXBNB  0.0  0.0   
1994  1491678.0 2021-09-16 05:35:06.215905+00:00  ADXBNB  0.0  0.0   
1995  1492426.0 2021-09-16 05:37:06.028755+00:00  ADXBNB  0.0  0.0   

                                   5    6    7    8    9   \
30   2021-09-13 11:37:54.144403+00:00  0.0  0.0  0.0  0.0   
31   2021-09-13 11:38:56

             0                                1       2    3    4   \
38      28590.0 2021-09-14 20:45:53.290947+00:00  ADXBNB  0.0  0.0   
39      29338.0 2021-09-14 20:46:54.240038+00:00  ADXBNB  0.0  0.0   
40      30086.0 2021-09-14 20:47:54.724975+00:00  ADXBNB  0.0  0.0   
41      30834.0 2021-09-14 20:48:53.080899+00:00  ADXBNB  0.0  0.0   
42      31582.0 2021-09-14 20:49:53.992041+00:00  ADXBNB  0.0  0.0   
...         ...                              ...     ...  ...  ...   
1995  1492426.0 2021-09-16 05:37:06.028755+00:00  ADXBNB  0.0  0.0   
1996  1493174.0 2021-09-16 05:39:07.410699+00:00  ADXBNB  0.0  0.0   
1997  1493922.0 2021-09-16 05:41:06.439065+00:00  ADXBNB  0.0  0.0   
1998  1494670.0 2021-09-16 05:43:07.506424+00:00  ADXBNB  0.0  0.0   
1999  1495418.0 2021-09-16 05:45:07.129474+00:00  ADXBNB  0.0  0.0   

                                   5    6    7    8    9   \
38   2021-09-13 11:45:53.290947+00:00  0.0  0.0  0.0  0.0   
39   2021-09-13 11:46:54.240038+00:00

             0                                1       2    3    4   \
46      34574.0 2021-09-14 20:53:53.142891+00:00  ADXBNB  0.0  0.0   
47      35322.0 2021-09-14 20:54:53.743993+00:00  ADXBNB  0.0  0.0   
48      36070.0 2021-09-14 20:55:53.770393+00:00  ADXBNB  0.0  0.0   
49      36818.0 2021-09-14 20:56:53.083645+00:00  ADXBNB  0.0  0.0   
50      37566.0 2021-09-14 20:57:53.668211+00:00  ADXBNB  0.0  0.0   
...         ...                              ...     ...  ...  ...   
1999  1495418.0 2021-09-16 05:45:07.129474+00:00  ADXBNB  0.0  0.0   
2000  1496166.0 2021-09-16 05:47:07.022297+00:00  ADXBNB  0.0  0.0   
2001  1496914.0 2021-09-16 05:49:06.750029+00:00  ADXBNB  0.0  0.0   
2002  1497662.0 2021-09-16 05:51:06.342737+00:00  ADXBNB  0.0  0.0   
2003  1498410.0 2021-09-16 05:53:06.980769+00:00  ADXBNB  0.0  0.0   

                                   5    6    7    8    9   \
46   2021-09-13 11:53:53.142891+00:00  0.0  0.0  0.0  0.0   
47   2021-09-13 11:54:53.743993+00:00

...

             0                                1       2    3    4   \
3476  2600451.0 2021-09-18 09:31:14.001101+00:00  ADXBNB  0.0  0.0   
3477  2601199.0 2021-09-18 09:33:13.409051+00:00  ADXBNB  0.0  0.0   
3478  2601947.0 2021-09-18 09:35:12.991738+00:00  ADXBNB  0.0  0.0   
3479  2602695.0 2021-09-18 09:37:13.534535+00:00  ADXBNB  0.0  0.0   
3480  2603443.0 2021-09-18 09:39:13.062400+00:00  ADXBNB  0.0  0.0   
...         ...                              ...     ...  ...  ...   
4406  3296091.0 2021-09-19 18:18:26.713787+00:00  ADXBNB  0.0  0.0   
4407  3296839.0 2021-09-19 18:21:27.700446+00:00  ADXBNB  0.0  0.0   
4408  3297587.0 2021-09-19 18:24:26.622412+00:00  ADXBNB  0.0  0.0   
4409  3298335.0 2021-09-19 18:27:27.149152+00:00  ADXBNB  0.0  0.0   
4410  3299083.0 2021-09-19 18:30:27.191027+00:00  ADXBNB  0.0  0.0   

                                   5    6    7    8    9   \
3476 2021-09-17 00:31:14.001101+00:00  0.0  0.0  0.0  0.0   
3477 2021-09-17 00:33:13.409051+00:00

             0                                1       2    3    4   \
3487  2608679.0 2021-09-18 09:53:13.617250+00:00  ADXBNB  0.0  0.0   
3488  2609427.0 2021-09-18 09:55:13.725159+00:00  ADXBNB  0.0  0.0   
3489  2610175.0 2021-09-18 09:57:13.903024+00:00  ADXBNB  0.0  0.0   
3490  2610923.0 2021-09-18 09:59:13.410941+00:00  ADXBNB  0.0  0.0   
3491  2611671.0 2021-09-18 10:01:13.233708+00:00  ADXBNB  0.0  0.0   
...         ...                              ...     ...  ...  ...   
4413  3301327.0 2021-09-19 18:39:27.196163+00:00  ADXBNB  0.0  0.0   
4414  3302075.0 2021-09-19 18:42:27.213068+00:00  ADXBNB  0.0  0.0   
4415  3302823.0 2021-09-19 18:45:27.205288+00:00  ADXBNB  0.0  0.0   
4416  3303571.0 2021-09-19 18:48:27.994223+00:00  ADXBNB  0.0  0.0   
4417  3304319.0 2021-09-19 18:51:27.733315+00:00  ADXBNB  0.0  0.0   

                                   5    6    7    8    9   \
3487 2021-09-17 00:53:13.617250+00:00  0.0  0.0  0.0  0.0   
3488 2021-09-17 00:55:13.725159+00:00

nannannannan
             0                                1       2    3    4   \
3499  2617655.0 2021-09-18 10:17:14.116458+00:00  ADXBNB  0.0  0.0   
3500  2618403.0 2021-09-18 10:19:14.389256+00:00  ADXBNB  0.0  0.0   
3501  2619151.0 2021-09-18 10:21:14.197172+00:00  ADXBNB  0.0  0.0   
3502  2619899.0 2021-09-18 10:23:13.729982+00:00  ADXBNB  0.0  0.0   
3503  2620647.0 2021-09-18 10:25:13.077856+00:00  ADXBNB  0.0  0.0   
...         ...                              ...     ...  ...  ...   
4421  3307311.0 2021-09-19 19:03:26.360626+00:00  ADXBNB  0.0  0.0   
4422  3308059.0 2021-09-19 19:06:27.157403+00:00  ADXBNB  0.0  0.0   
4423  3308807.0 2021-09-19 19:09:27.489094+00:00  ADXBNB  0.0  0.0   
4424  3309555.0 2021-09-19 19:12:26.760882+00:00  ADXBNB  0.0  0.0   
4425  3310303.0 2021-09-19 19:15:26.842616+00:00  ADXBNB  0.0  0.0   

                                   5    6    7    8    9   \
3499 2021-09-17 01:17:14.116458+00:00  0.0  0.0  0.0  0.0   
3500 2021-09-17 01:19:14

             0                                1       2    3    4   \
3505  2622143.0 2021-09-18 10:29:13.913534+00:00  ADXBNB  0.0  0.0   
3506  2622891.0 2021-09-18 10:31:13.381448+00:00  ADXBNB  0.0  0.0   
3507  2623639.0 2021-09-18 10:33:14.144234+00:00  ADXBNB  0.0  0.0   
3508  2624387.0 2021-09-18 10:35:13.742243+00:00  ADXBNB  0.0  0.0   
3509  2625135.0 2021-09-18 10:37:13.515053+00:00  ADXBNB  0.0  0.0   
...         ...                              ...     ...  ...  ...   
4425  3310303.0 2021-09-19 19:15:26.842616+00:00  ADXBNB  0.0  0.0   
4426  3311051.0 2021-09-19 19:18:27.289568+00:00  ADXBNB  0.0  0.0   
4427  3311799.0 2021-09-19 19:21:26.306282+00:00  ADXBNB  0.0  0.0   
4428  3312547.0 2021-09-19 19:24:27.433079+00:00  ADXBNB  0.0  0.0   
4429  3313295.0 2021-09-19 19:27:26.749818+00:00  ADXBNB  0.0  0.0   

                                   5    6    7    8    9   \
3505 2021-09-17 01:29:13.913534+00:00  0.0  0.0  0.0  0.0   
3506 2021-09-17 01:31:13.381448+00:00

KeyboardInterrupt: 